In [1]:
# Notebook to transform segmented images into np array and clean CSV

In [60]:
# Python ≥3.5 is required

import sys
assert sys.version_info >= (3, 5)

import numpy as np
import pandas as pd
import os

from PIL import Image as PIL_Image
import timeit

# To plot figures
%matplotlib inline
import matplotlib as mpl
import matplotlib.pyplot as plt
mpl.rc('axes', labelsize=14)
mpl.rc('xtick', labelsize=12)
mpl.rc('ytick', labelsize=12)

In [2]:
# Specifying paths for output

In [3]:
# Where to save
# the figures from pre-processing

PROJECT_ROOT_DIR = "output"
CHAPTER_ID = "segmentation"

IMAGES_PATH = os.path.join(PROJECT_ROOT_DIR, "figures", CHAPTER_ID)
os.makedirs(IMAGES_PATH, exist_ok=True)

def save_fig(fig_id, tight_layout=True, fig_extension="png", resolution=300):
    path = os.path.join(IMAGES_PATH, fig_id + "." + fig_extension)
    print("Saving figure", fig_id)
    if tight_layout:
        plt.tight_layout()
    plt.savefig(path, format=fig_extension, dpi=resolution)

In [4]:
# Specifying paths and switch for image data

In [61]:
# Implement a switch between dummy and full image data
full_data_switch_on = False # if the full data set should be used, this switch need to be set to true

In [47]:
#train_switch = True  # Set False for Test
# je nachdem ob wir ein test-csv bekommen, müssen wir das train_set selber in test&train splitten


In [62]:
if full_data_switch_on == False:
    #set path to sample data set
    ROOT_PATH_DATA = "input/"
    PATH_DATA_TRAIN = os.path.join(ROOT_PATH_DATA + "03_segmented/train/sample_segmented_images/seg_train_sample_100")
    LABEL_DATA_PATH = os.path.join(ROOT_PATH_DATA + "01_raw/train_sample_100.csv")
elif full_data_switch_on == True:
    #set path to the full data set
    ROOT_PATH_DATA = "input/"
    PATH_DATA_TRAIN = os.path.join(ROOT_PATH_DATA + "03_segmented/train/full_set_segmented_images")
    PATH_DATA_TEST = os.path.join(ROOT_PATH_DATA + "03_segmented/test/full_set_segmented_images") 
    LABEL_DATA_PATH = os.path.join(ROOT_PATH_DATA + "01_raw/train.csv")
    #csv for test not available yet 
else:
    raise ValueError("Full data switch is not correctly defined")

In [49]:
## Getting an overview of the data - checking out CSV

In [63]:
label_train_df = pd.read_csv(LABEL_DATA_PATH, sep = ';') #NOTE: separation is different between raw csv and segmented csv

In [64]:
label_train_df.head(10)

image             species individual_id
0  0a572d02a1ed8e.png         minke_whale  0940fc2c3809
1  0a0ae8699f1a5a.png              beluga  af02c0601c6e
2  0a0cedc8ac6499.png  melon_headed_whale  fa870e1ae82d
3  0a0d83708b4fdc.png  bottlenose_dolphin  c2705f9e75c8
4  0a0e4b82b9f3ee.png      humpback_whale  02f5c5ee9c2a
5  0a0e90fb154acf.png  false_killer_whale  f7bb4f9a9d1a
6  0a0f53c069bffc.png     spinner_dolphin  1b9d07e72110
7  0a01b620a7915b.png          blue_whale  7c9f2b782eed
8  0a1bcf1da2b695.png              beluga  d53bc5d9dbfe
9  0a1c741127059b.png  bottlenose_dolphin  a43daee90cbc

In [65]:
label_train_df['species']. value_counts()

beluga                       20
bottlenose_dolphin           17
humpback_whale               16
blue_whale                    7
spinner_dolphin               6
minke_whale                   4
false_killer_whale            4
kiler_whale                   3
melon_headed_whale            3
bottlenose_dolpin             2
long_finned_pilot_whale       2
common_dolphin                2
dusky_dolphin                 2
short_finned_pilot_whale      2
fin_whale                     2
pantropic_spotted_dolphin     1
killer_whale                  1
cuviers_beaked_whale          1
southern_right_whale          1
gray_whale                    1
spotted_dolphin               1
pilot_whale                   1
pygmy_killer_whale            1
Name: species, dtype: int64

In [53]:
#We have some typos in the species:

#E.g., there is bottlenose_dolphin and bottlenose_dolpin, kiler_whale and killer_whale. 
#Obviously, it is typos. Also, globis and pilot_whale are short_finned_pilot_whale

#We thus need to correct the labels:

In [66]:
label_train_df.species.replace({"globis": "short_finned_pilot_whale",
                          "pilot_whale": "short_finned_pilot_whale",
                          "kiler_whale": "killer_whale",
                          "bottlenose_dolpin": "bottlenose_dolphin"}, inplace=True)

In [67]:
label_train_df['species']. value_counts()

beluga                       20
bottlenose_dolphin           19
humpback_whale               16
blue_whale                    7
spinner_dolphin               6
minke_whale                   4
killer_whale                  4
false_killer_whale            4
melon_headed_whale            3
short_finned_pilot_whale      3
long_finned_pilot_whale       2
common_dolphin                2
dusky_dolphin                 2
fin_whale                     2
pantropic_spotted_dolphin     1
cuviers_beaked_whale          1
southern_right_whale          1
gray_whale                    1
spotted_dolphin               1
pygmy_killer_whale            1
Name: species, dtype: int64

In [68]:
def store_csv(label_df):
    if full_data_switch_on == True:
        label_df.to_csv("input/04_cleaned/train/clean_train.csv", sep=';')
        print("dataframe successfully stored in: input/04_cleaned/train")
    elif full_data_switch_on == False:
        label_df.to_csv("input/04_cleaned/train/clean_sample_train.csv", sep=';')
        print("dataframe successfully stored in: input/04_cleaned/train")
    else:
        raise ValueError("Full data switch is not correctly defined")

In [69]:
store_csv(label_train_df)

dataframe successfully stored in: input/04_cleaned/train


In [58]:
# Function to transform images into np.array

In [70]:
# Defining function to list all pictures to include
def list_files(dir):
    r = []
    for root, dirs, files in os.walk(dir):
        for name in files:
            r.append(os.path.join(root, name))
    return r

In [60]:
# define filepaths for sample and full image data
if full_data_switch_on == True:
    filepaths_test = list_files(PATH_DATA_TEST)

In [71]:
filepaths_train = list_files(PATH_DATA_TRAIN)

In [72]:
filepaths_train

['input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a100ed55f1c7e.png',
 'input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a0cedc8ac6499.png',
 'input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a9f092e4e3e92.png',
 'input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a07fcc5ab1b4d.png',
 'input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a3f7ed710605e.png',
 'input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a1bcf1da2b695.png',
 'input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a4ef0609c5bb9.png',
 'input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a99ad33a87739.png',
 'input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a23cedc1e719e.png',
 'input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a39e7972b191c.png',
 'input/03_segmented/train/sample_segmented_images/seg_train_sample_10

In [57]:
def pixel_transform(target_pixel):

    # Run-time information
    start_time = timeit.default_timer()
    print(">... Starting pixel transformation for train images for resolution: ", target_pixel, "x", target_pixel)

    # Initialize emtpy array of fitting length
    array_length = target_pixel*target_pixel*3 #Times 3 as we have 3 values (RGB) per pixel
    loaded_pics_train = np.empty([0,array_length])

    dim = (target_pixel, target_pixel)

    #Running trough all train image files
    for filename in filepaths_train:
        image_np = cv2.imread(filename)
        image_np = image_np.resize(dim)
        # Include help array to reshape 3D-array(e.g.: 1024, 1024, 3) into 1D array
        image_np = np.reshape(image_np,(image_np.size,))
        # Stack each array onto each other to have one larger array of shape (#obs,#pixels*3)
        loaded_pics_train = np.vstack((loaded_pics_train, image_np))

        # Show progress
        print("Transformed image", filename)

    #End run-time information
    elapsed = timeit.default_timer() - start_time
    print("Finished", target_pixel, "x", target_pixel ,"pixel transformation for train images. Run-time in seconds: ", round(elapsed,2))

    # Returning
    return loaded_pics_train

In [58]:
image_data_train_sample_1 = pixel_transform(224)


>... Starting pixel transformation for train images for resolution:  224 x 224


AttributeError: 'NoneType' object has no attribute 'size'

In [73]:
# Defining function that performs translation of jpg files into numerical representation
def pixel_transformation(target_pixel,train_switch):
    
    if train_switch == True:
        
        # Run-time information
        start_time = timeit.default_timer()
        print(">... Starting pixel transformation for train images for resolution: ", target_pixel, "x", target_pixel)

        # Initialize emtpy array of fitting length
        array_length = target_pixel*target_pixel*3 #Times 3 as we have 3 values (RGB) per pixel
        loaded_pics_train = np.empty([0,array_length])

        #Running trough all train image files
        for filename in filepaths_train:
            # open picture
            pic = PIL_Image.open(filename)
            # Reduce size from original format to target format
            # pic_resized = pic.resize((target_pixel, target_pixel), PIL_Image.NEAREST)
            # Extract RGB data
            pic_data = np.asarray(pic.resize((target_pixel, target_pixel), PIL_Image.NEAREST))
            # Include help array to reshape 3D-array(e.g.: 1024, 1024, 3) into 1D array
            help_array = np.reshape(pic_data,(pic_data.size,))
            # Stack each array onto each other to have one larger array of shape (#obs,#pixels*3)
            loaded_pics_train = np.vstack((loaded_pics_train, help_array))
            # Close picture
            pic.close()
            pic.readonly = False
            # Show progress
            print("Transformed image", filename)
        
        #End run-time information
        elapsed = timeit.default_timer() - start_time
        print("Finished", target_pixel, "x", target_pixel ,"pixel transformation for train images. Run-time in seconds: ", round(elapsed,2))
 
        # Returning
        return loaded_pics_train # array with dimension pixels x pixels x colors for each image
    
    elif train_switch == False:
        
        # Run-time information
        start_time = timeit.default_timer()
        print(">... Starting pixel transformation for test images for resolution: ", target_pixel, "x", target_pixel)

        # Initialize emtpy array of fitting length
        array_length = target_pixel*target_pixel*3 #Times 3 as we have 3 values (RGB) per pixel
        loaded_pics_test = np.empty([0,array_length])

        #Running trough all train image files
        for filename in filepaths_test:
            # open picture
            pic = PIL_Image.open(filename)
            # Reduce size from original format to target format
            pic_resized = pic.resize((target_pixel, target_pixel))
            # Extract RGB data
            pic_data = np.asarray(pic_resized)
            # Include help array to reshape 3D-array(e.g.: 1024, 1024, 3) into 1D array
            help_array = np.reshape(pic_data,(pic_data.size,))
            # Stack each array onto each other to have one larger array of shape (#obs,#pixels*3)
            loaded_pics_test = np.vstack((loaded_pics_test, help_array))
            # Close picture
            pic.close()
            pic.readonly = False
            # Show progres
            print("Transformed image", filename)
        
        #End run-time information
        elapsed = timeit.default_timer() - start_time
        print("Finished", target_pixel, "x", target_pixel ,"pixel transformation for test images. Run-time in seconds: ", round(elapsed,2))
 
        # Returning
        return loaded_pics_test # array with dimension pixels x pixels x colors for each image
    
    else:
        print("train switch is not defined correctly")

In [ ]:
# make transformation for test data, train data, sample data
# depending on full_data_swtich_on configuration, the transformation is done for FULL data set (test or train) or for SAMPLE data set (only train)
# if the function is called, the train_switch must be set to True or False

In [74]:
image_data_train_sample = pixel_transformation(48, train_switch=True)

>... Starting pixel transformation for train images for resolution:  48 x 48
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a100ed55f1c7e.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a0cedc8ac6499.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a9f092e4e3e92.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a07fcc5ab1b4d.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a3f7ed710605e.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a1bcf1da2b695.png


/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/ipykernel_launcher.py:21: DeprecationWarning: NEAREST is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.NEAREST or Dither.NONE instead.


Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a4ef0609c5bb9.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a99ad33a87739.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a23cedc1e719e.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a39e7972b191c.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a93b0a0d4f3a7.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a97d1e6751b0d.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a7dd6215c0916.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a6da6533bd494.png
Transformed image input/03_segmented/train/sample_segmented_images/seg_train_sample_100/0a5f343d8435ce.png
Transformed image input/03_segmented/

In [75]:
image_data_train_sample.shape

(100, 6912)

In [64]:
# turn full_data_switch_on to true and apply functions above before 
image_data_full_train = pixel_transformation(48, train_switch=True)
# image_data_full_test = pixel_transformation(224, train_switch=False)

>... Starting pixel transformation for train images for resolution:  48 x 48
Transformed image input/03_segmented/train/full_set_segmented_images/907a1e10ce8ea0.png
Transformed image input/03_segmented/train/full_set_segmented_images/6dec8822432532.png
Transformed image input/03_segmented/train/full_set_segmented_images/51483fd54eb2c3.png
Transformed image input/03_segmented/train/full_set_segmented_images/95b704dfd194ba.png
Transformed image input/03_segmented/train/full_set_segmented_images/dde9205da249b1.png
Transformed image input/03_segmented/train/full_set_segmented_images/95792f994f5898.png
Transformed image input/03_segmented/train/full_set_segmented_images/d7dba0d7a94096.png
Transformed image input/03_segmented/train/full_set_segmented_images/171422bdc0fe3e.png
Transformed image input/03_segmented/train/full_set_segmented_images/5c2f03ca2bc401.png
Transformed image input/03_segmented/train/full_set_segmented_images/78ec91797e4941.png
Transformed image input/03_segmented/train/

Transformed image input/03_segmented/train/full_set_segmented_images/c0a0ab4ba262cc.png
Transformed image input/03_segmented/train/full_set_segmented_images/8b881dde7361ae.png
Transformed image input/03_segmented/train/full_set_segmented_images/b767b86cb8fc9a.png
Transformed image input/03_segmented/train/full_set_segmented_images/1299773abd1566.png
Transformed image input/03_segmented/train/full_set_segmented_images/8804b02c19eda5.png
Transformed image input/03_segmented/train/full_set_segmented_images/f33147f49406b1.png
Transformed image input/03_segmented/train/full_set_segmented_images/57fe6b85d92c65.png
Transformed image input/03_segmented/train/full_set_segmented_images/613e017de4bae6.png
Transformed image input/03_segmented/train/full_set_segmented_images/4c2a894ec3e2f7.png
Transformed image input/03_segmented/train/full_set_segmented_images/788e22acc64500.png
Transformed image input/03_segmented/train/full_set_segmented_images/fb401e3e25368b.png
Transformed image input/03_segme

Transformed image input/03_segmented/train/full_set_segmented_images/5d549f5ee3bd6c.png
Transformed image input/03_segmented/train/full_set_segmented_images/ea0ff0f86d30e8.png
Transformed image input/03_segmented/train/full_set_segmented_images/7003adf4cf857d.png
Transformed image input/03_segmented/train/full_set_segmented_images/f53bf9306bc279.png
Transformed image input/03_segmented/train/full_set_segmented_images/51801d64f2900d.png
Transformed image input/03_segmented/train/full_set_segmented_images/8b2fde7551f482.png
Transformed image input/03_segmented/train/full_set_segmented_images/48e5b031baf093.png
Transformed image input/03_segmented/train/full_set_segmented_images/e802722d13abc4.png
Transformed image input/03_segmented/train/full_set_segmented_images/eb15a51b62441f.png
Transformed image input/03_segmented/train/full_set_segmented_images/64ccb08fd2dd99.png
Transformed image input/03_segmented/train/full_set_segmented_images/2fd46bd18e62b0.png
Transformed image input/03_segme

Transformed image input/03_segmented/train/full_set_segmented_images/840b5daaf25729.png
Transformed image input/03_segmented/train/full_set_segmented_images/ead7428de2d3a4.png
Transformed image input/03_segmented/train/full_set_segmented_images/3f75bc1d6165da.png
Transformed image input/03_segmented/train/full_set_segmented_images/d4729f87ccccb3.png
Transformed image input/03_segmented/train/full_set_segmented_images/7c2318ecc68848.png
Transformed image input/03_segmented/train/full_set_segmented_images/5011dec169808d.png
Transformed image input/03_segmented/train/full_set_segmented_images/6c34c6119a9931.png
Transformed image input/03_segmented/train/full_set_segmented_images/2e388e3917e0fe.png
Transformed image input/03_segmented/train/full_set_segmented_images/7cf9fb511acaab.png
Transformed image input/03_segmented/train/full_set_segmented_images/000bef247c7a42.png
Transformed image input/03_segmented/train/full_set_segmented_images/00e6b936f02c6e.png
Transformed image input/03_segme

Transformed image input/03_segmented/train/full_set_segmented_images/7998476ba2d328.png
Transformed image input/03_segmented/train/full_set_segmented_images/dc18efbb3a8420.png
Transformed image input/03_segmented/train/full_set_segmented_images/010134d3eeb07e.png
Transformed image input/03_segmented/train/full_set_segmented_images/96cce6f082886e.png
Transformed image input/03_segmented/train/full_set_segmented_images/3e2722805fd49f.png
Transformed image input/03_segmented/train/full_set_segmented_images/ecf59c1a493d0c.png
Transformed image input/03_segmented/train/full_set_segmented_images/0b259aea348667.png
Transformed image input/03_segmented/train/full_set_segmented_images/c739092b9f1d1d.png
Transformed image input/03_segmented/train/full_set_segmented_images/022cb725f51c9a.png
Transformed image input/03_segmented/train/full_set_segmented_images/6bc40b4c70de71.png
Transformed image input/03_segmented/train/full_set_segmented_images/09f93846930a21.png
Transformed image input/03_segme

...

Transformed image input/03_segmented/train/full_set_segmented_images/8f4ae8165681fb.png
Transformed image input/03_segmented/train/full_set_segmented_images/79d7ef013f6c7f.png
Transformed image input/03_segmented/train/full_set_segmented_images/6b7f12b2848b4d.png
Transformed image input/03_segmented/train/full_set_segmented_images/1291b89eb35c9c.png
Transformed image input/03_segmented/train/full_set_segmented_images/27e720f8b247d3.png
Transformed image input/03_segmented/train/full_set_segmented_images/252cf6b02dd108.png
Transformed image input/03_segmented/train/full_set_segmented_images/26638c05b454b8.png
Transformed image input/03_segmented/train/full_set_segmented_images/f9a12c90257f3a.png
Transformed image input/03_segmented/train/full_set_segmented_images/11f0407bafb755.png
Transformed image input/03_segmented/train/full_set_segmented_images/0135e7c19d415c.png
Transformed image input/03_segmented/train/full_set_segmented_images/57d41a20f5ca44.png
Transformed image input/03_segme

Transformed image input/03_segmented/train/full_set_segmented_images/f9af1be161e498.png
Transformed image input/03_segmented/train/full_set_segmented_images/d4894380323c06.png
Transformed image input/03_segmented/train/full_set_segmented_images/4d83b0adc9a584.png
Transformed image input/03_segmented/train/full_set_segmented_images/da4fa2c961e2aa.png
Transformed image input/03_segmented/train/full_set_segmented_images/847addb1d0a414.png
Transformed image input/03_segmented/train/full_set_segmented_images/809611aff0bfbb.png
Transformed image input/03_segmented/train/full_set_segmented_images/affd3cd44721d6.png
Transformed image input/03_segmented/train/full_set_segmented_images/951f603c1b5303.png
Transformed image input/03_segmented/train/full_set_segmented_images/1f430a701c4e5b.png
Transformed image input/03_segmented/train/full_set_segmented_images/143bf0d181aba4.png
Transformed image input/03_segmented/train/full_set_segmented_images/6af7f964305efa.png
Transformed image input/03_segme

Transformed image input/03_segmented/train/full_set_segmented_images/821df11ac39de0.png
Transformed image input/03_segmented/train/full_set_segmented_images/61e13d0e20fd9b.png
Transformed image input/03_segmented/train/full_set_segmented_images/284fdece6beeda.png
Transformed image input/03_segmented/train/full_set_segmented_images/50d203cd9284b0.png
Transformed image input/03_segmented/train/full_set_segmented_images/2cccac27a5969e.png
Transformed image input/03_segmented/train/full_set_segmented_images/d930cf6b7b4d3e.png
Transformed image input/03_segmented/train/full_set_segmented_images/c0531e6ac59b5e.png
Transformed image input/03_segmented/train/full_set_segmented_images/9f33c0c5fe0ceb.png
Transformed image input/03_segmented/train/full_set_segmented_images/fc7039af6bd6cb.png
Transformed image input/03_segmented/train/full_set_segmented_images/bc3f0d4efbf182.png
Transformed image input/03_segmented/train/full_set_segmented_images/d2fc13fdcbfc38.png
Transformed image input/03_segme

Transformed image input/03_segmented/train/full_set_segmented_images/4eaad505877d23.png
Transformed image input/03_segmented/train/full_set_segmented_images/cee2ec9d6daa89.png
Transformed image input/03_segmented/train/full_set_segmented_images/f8787887353ba2.png
Transformed image input/03_segmented/train/full_set_segmented_images/f28a6db1cd9584.png
Transformed image input/03_segmented/train/full_set_segmented_images/e58c5afe561294.png
Transformed image input/03_segmented/train/full_set_segmented_images/50984c6a2134aa.png
Transformed image input/03_segmented/train/full_set_segmented_images/bd11dbcec012f3.png
Transformed image input/03_segmented/train/full_set_segmented_images/7da75a0fada16f.png
Transformed image input/03_segmented/train/full_set_segmented_images/a66e704511b926.png
Transformed image input/03_segmented/train/full_set_segmented_images/aa7bb9c6df1198.png
Transformed image input/03_segmented/train/full_set_segmented_images/2938a4df7fe742.png
Transformed image input/03_segme

Transformed image input/03_segmented/train/full_set_segmented_images/a421790d31efbd.png
Transformed image input/03_segmented/train/full_set_segmented_images/d953cbc2037c53.png
Transformed image input/03_segmented/train/full_set_segmented_images/cc06ca775ba548.png
Transformed image input/03_segmented/train/full_set_segmented_images/5d24020c69b993.png
Transformed image input/03_segmented/train/full_set_segmented_images/37e198e1caaeb3.png
Transformed image input/03_segmented/train/full_set_segmented_images/21879fec3edf9a.png
Transformed image input/03_segmented/train/full_set_segmented_images/fd44787a003869.png
Transformed image input/03_segmented/train/full_set_segmented_images/a96e6649c03a0a.png
Transformed image input/03_segmented/train/full_set_segmented_images/8890be82d4a136.png
Transformed image input/03_segmented/train/full_set_segmented_images/0618e60a7082ec.png
Transformed image input/03_segmented/train/full_set_segmented_images/3e6d2a457b3300.png
Transformed image input/03_segme

In [65]:
image_data_full_train.shape

(51033, 6912)

In [ ]:
# define function to store np.arrays in respective data folders

In [76]:
from numpy import savez_compressed

In [77]:
def store_dict_train(image_df, target_pixel):
    
    if full_data_switch_on == True:
        savez_compressed("input/04_cleaned/train/img_data_full_"+str(target_pixel)+".npz",image_df)
        print("file successfully stored in: input/04_cleaned/train/img_data_full_"+str(target_pixel)+".npz")
        
    elif full_data_switch_on == False:
        savez_compressed("input/04_cleaned/train/img_data_sample_"+str(target_pixel)+".npz",image_df)
        print("file successfully stored in: input/04_cleaned/train/img_data_sample_"+str(target_pixel)+".npz")
        
    else:
        raise ValueError("Full data switch is not correctly defined")

In [48]:
def store_dict_test(image_df,target_pixel):
    savez_compressed("input/04_cleaned/test/img_data_full_"+str(target_pixel)+".npz",image_df)
    print("file successfully stored in: input/04_cleaned/test/img_data_full_"+str(target_pixel)+".npz")


In [78]:
store_dict_train(image_data_train_sample,target_pixel=48)

file successfully stored in: input/04_cleaned/train/img_data_sample_48.npz


In [ ]:
store_dict_train(image_data_full_train,target_pixel=48)